In [1]:
!pip install -qU pinecone-client \
                 tqdm \
                 httpimport \
                 requests

ERROR: After October 2020 you may experience errors when installing or updating packages. This is because pip will change the way that it resolves dependency conflicts.

We recommend you use --use-feature=2020-resolver to test your packages with the new resolver before it becomes the default.

mediapipe 0.8.1 requires opencv-python, which is not installed.
djitellopy 2.4.0 requires opencv-python, which is not installed.
umojahack2023 0.1 requires numpy==1.23.5, but you'll have numpy 1.24.4 which is incompatible.
tensorflow 2.11.0 requires gast<=0.4.0,>=0.2.1, but you'll have gast 0.5.3 which is incompatible.
streamlit 1.3.1 requires click<8.0,>=7.0, but you'll have click 8.1.3 which is incompatible.
pandas-profiling 3.2.0 requires joblib~=1.1.0, but you'll have joblib 1.2.0 which is incompatible.
pandas-profiling 3.2.0 requires markupsafe~=2.1.1, but you'll have markupsafe 2.0.1 which is incompatible.
mediapipe 0.8.1 requires numpy==1.19.3, but you'll have numpy 1.24.4 which is incompa

In [2]:
import os
import requests

import tqdm
import httpimport
import pinecone
import numpy as np
from PIL import Image

DATA_DIRECTORY = 'tmp'
INDEX_NAME = 'jumia-product-search'
INDEX_DIMENSION = 512
BATCH_SIZE=200

/Users/paul/miniconda3/lib/python3.8/site-packages/pinecone/index.py:4: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [3]:
PINECONE_API_KEY = "22e8b95b-18a6-42b4-8824-dc65f08a60e1"
PINECONE_ENV = "us-west1-gcp-free"

In [4]:
pinecone.init(api_key= PINECONE_API_KEY,
              environment=PINECONE_ENV)


In [7]:
index_name = 'jumia-product-embeddings'

if index_name not in pinecone.list_indexes():
    # now create the new index
    pinecone.create_index(
        index_name,
        dimension= 512,  # 768
        metric='cosine',
        pod_type='s1',
        pods=1
    )

# connect to index
index = pinecone.Index(index_name)
# then check index status
index.describe_index_stats()

{'dimension': 512,
 'index_fullness': 0.0,
 'namespaces': {},
 'total_vector_count': 0}

In [8]:
import joblib


EMBED_FILE = "../image_search_engine/artifacts/embeddings/embed_2023-07-09_15-17-45.pkl"


def load_serialized_object(file_path):
    try:
        obj = joblib.load(file_path)
        return obj
    except FileNotFoundError:
        print(f"File not found: {file_path}")
    except Exception as e:
        print(f"Error loading serialized object: {str(e)}")

In [12]:
embeddings = load_serialized_object(EMBED_FILE)

In [48]:
embeddings = [embed.tolist() for embed in embeddings]


In [10]:
len(embed)

2941

In [15]:
import json
def load_json_file(file_path):
    with open(file_path, "r") as file:
        data = json.load(file)
    return data

In [16]:
json_data = load_json_file("processed/jumia_3650/jumia_3650.json")

In [19]:
from tqdm.auto import tqdm

batch_size = 300
n_embed = len(embeddings)  # number of records to index from each language

for i in tqdm(range(0, 5)):
    embed = embeddings[i]
    id_ = f"JUMIA3650.{i}"
    metadata = json_data[i]
    
    print([id_, embed[:3], metadata])
#     index.upsert(zip(ids, embeds, metadata))

  0%|          | 0/5 [00:00<?, ?it/s]

['JUMIA3650.0', array([ 0.01932903, -1.791061  ,  1.3284612 ], dtype=float32), {'filename': 'product_ear_pods_401_0.jpg', 'product_id': 'product_ear_pods_401', 'product_category': 'ear_pods', 'product_name': 'Power Pod Fingerprint Touch Bluetooth 5.0 Wireless Stereo Hear Phone Pod', 'product_image_url': 'https://ng.jumia.is/unsafe/fit-in/680x680/filters:fill(white)/product/66/4640212/1.jpg?9552', 'product_url': 'https://www.jumia.com.ng/power-pod-fingerprint-touch-bluetooth-5.0-wireless-stereo-hear-phone-pod-212046466.html', 'discounted_price': '₦ 6,500', 'original_price': '₦ 8,500'}]
['JUMIA3650.1', array([ 0.12243042, -1.9603508 ,  2.0345879 ], dtype=float32), {'filename': 'product_headset_671_3.jpg', 'product_id': 'product_headset_671', 'product_category': 'headset', 'product_name': 'Solar Charging Bluetooth Earphone Wireless TWS Headset', 'product_image_url': 'https://ng.jumia.is/unsafe/fit-in/680x680/filters:fill(white)/product/43/4238202/1.jpg?0528', 'product_url': 'https://www.j

In [49]:
batch_size = 300
n_embed = len(embeddings)  # number of records to index from each language



upsert = []
for i in tqdm(range(0, n_embed, batch_size)):
    ids = [f"JUMIA_3650.{idx}" for idx in range(i, i+batch_size)]
    batch_embeddings = embeddings[i:i+batch_size]
    batch_metadata = json_data[i:i+batch_size]
        
    index.upsert(zip(ids, batch_embeddings, batch_metadata))

  0%|          | 0/10 [00:00<?, ?it/s]

In [50]:
index.describe_index_stats()

{'dimension': 512,
 'index_fullness': 0.0,
 'namespaces': {'': {'vector_count': 2941}},
 'total_vector_count': 2941}

In [41]:
len(embeddings[i:i+batch_size])

300

In [32]:
upsert[1][2]

('JUMIA_3650.302',
 {'filename': 'product_usb_hub_181_2.jpg',
  'product_id': 'product_usb_hub_181',
  'product_category': 'usb_hub',
  'product_name': '4 Ports USB Hub High Speed Adapter For DESKTOP LAPTOP Black Black',
  'product_image_url': 'https://ng.jumia.is/unsafe/fit-in/680x680/filters:fill(white)/product/42/215709/1.jpg?7924',
  'product_url': 'https://www.jumia.com.ng/generic-4-ports-usb-hub-high-speed-adapter-for-desktop-laptop-black-black-90751224.html',
  'discounted_price': '₦ 2,355',
  'original_price': '₦ 3,533'})